In [1]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import requests

pd.set_option('display.max_columns', None)

## Loading datasets

In [2]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'repository_metadata.content_subjects': ast.literal_eval,
                                    'repository_metadata.name': ast.literal_eval,
                                    'repository_metadata.alternativename': ast.literal_eval,
                                    'repository_metadata.content_types': ast.literal_eval,
                                    'organization': ast.literal_eval
                                    },
                         dtype={'system_metadata.id': str})

opendoar_df.head()

system_metadata.id                           repository_metadata.name  \
0                134  {'name': 'eldorado - repository of the tu dort...   
1                 58  {'name': 'archive ouverte en sciences de linfo...   
2                 93  {'name': 'digitalcommons@the texas medical cen...   
3                 68  {'name': 'cognitive sciences eprint archive', ...   
4                 84  {'name': 'digital commons@carleton college', '...   

                 repository_metadata.alternativename  \
0  [{'name': 'eldorado - ressourcen aus und für l...   
1                        [{'acronym': '@rchivesic'}]   
2                                                 []   
3                         [{'acronym': 'cogprints'}]   
4                                                 []   

                  repository_metadata.url  repository_metadata.description  \
0         https://eldorado.tu-dortmund.de                              NaN   
1         https://archivesic.ccsd.cnrs.fr                              NaN   
2  http://digitalcommons.library.tmc.edu/                              NaN   
3                   http://cogprints.org/                              NaN   
4     http://digitalcommons.carleton.edu/                              NaN   

  repository_metadata.type repository_metadata.content_languages  \
0            institutional                                    []   
1            institutional                                    []   
2            institutional                                    []   
3             disciplinary                                    []   
4            institutional                                    []   

  system_metadata.date_modified system_metadata.date_created  \
0           2022-01-12 15:34:54          2005-12-19 14:57:52   
1           2022-01-12 15:34:53          2006-01-13 12:48:32   
2           2022-01-12 15:34:53          2006-02-14 11:16:12   
3           2022-01-12 15:34:53          2006-01-04 15:01:23   
4           2022-01-12 15:34:53          2006-01-04 16:07:58   

                repository_metadata.content_subjects  \
0  [arts, humanities, science, mathematics, socia...   
1  [arts, science, technology, engineering, mathe...   
2                              [health and medicine]   
3  [humanities, health and medicine, science, soc...   
4             [humanities, science, social sciences]   

                   repository_metadata.content_types  \
0  [journal_articles, conference_and_workshop_pap...   
1  [journal_articles, conference_and_workshop_pap...   
2       [journal_articles, theses_and_dissertations]   
3  [journal_articles, conference_and_workshop_pap...   
4  [journal_articles, unpub_reports_and_working_p...   

                                        organization policy_urls  \
0  [{'name': 'technische universität dortmund', '...          []   
1  [{'name': 'centre pour la communication scient...          []   
2  [{'name': 'texas medical center', 'alternative...          []   
3  [{'name': 'university of southampton', 'altern...          []   
4  [{'name': 'carleton college', 'alternativeName...          []   

         repository_metadata.software  \
0   {"name": "dspace", "version": ""}   
1      {"name": "hal", "version": ""}   
2    {"name": "other", "version": ""}   
3  {"name": "eprints", "version": ""}   
4    {"name": "other", "version": ""}   

                       repository_metadata.oai_url  \
0      https://eldorado.tu-dortmund.de/oai/request   
1  https://api.archives-ouvertes.fr/oai/archivesic   
2    http://digitalcommons.library.tmc.edu/do/oai/   
3                    http://cogprints.org/cgi/oai2   
4                                              NaN   

  system_metadata.publicly_visible  repository_metadata.repository_status  \
0                              yes                                    NaN   
1                              yes                                    NaN   
2                              yes                               

In [3]:
opendoar_df.columns

Index(['system_metadata.id', 'repository_metadata.name',
       'repository_metadata.alternativename', 'repository_metadata.url',
       'repository_metadata.description', 'repository_metadata.type',
       'repository_metadata.content_languages',
       'system_metadata.date_modified', 'system_metadata.date_created',
       'repository_metadata.content_subjects',
       'repository_metadata.content_types', 'organization', 'policy_urls',
       'repository_metadata.software', 'repository_metadata.oai_url',
       'system_metadata.publicly_visible',
       'repository_metadata.repository_status',
       'repository_metadata.fulltext_record_count',
       'repository_metadata.metadata_record_count'],
      dtype='object')

In [4]:
def empty_list_is_nan(cell):
    if isinstance(cell, list):
        return np.nan if len(cell) == 0 else cell
    else:
        return cell
    
opendoar_df = opendoar_df.applymap(empty_list_is_nan)

In [5]:
opendoar_df.describe(include='all')

system_metadata.id            repository_metadata.name  \
count                5811                                5811   
unique               5811                                5780   
top                   134  {'name': 'arch', 'language': 'en'}   
freq                    1                                   3   
mean                  NaN                                 NaN   
std                   NaN                                 NaN   
min                   NaN                                 NaN   
25%                   NaN                                 NaN   
50%                   NaN                                 NaN   
75%                   NaN                                 NaN   
max                   NaN                                 NaN   

       repository_metadata.alternativename  \
count                                 2155   
unique                                2115   
top                  [{'acronym': 'aura'}]   
freq                                     4   
mean                                   NaN   
std                                    NaN   
min                                    NaN   
25%                                    NaN   
50%                                    NaN   
75%                                    NaN   
max                                    NaN   

                   repository_metadata.url  repository_metadata.description  \
count                                 5810                              0.0   
unique                                5772                              NaN   
top     http://harp.lib.hiroshima-u.ac.jp/                              NaN   
freq                                     3                              NaN   
mean                                   NaN                              NaN   
std                                    NaN                              NaN   
min                                    NaN                              NaN   
25%                                    NaN                              NaN   
50%                                    NaN                              NaN   
75%                                    NaN                              NaN   
max                                    NaN                              NaN   

       repository_metadata.type repository_metadata.content_languages  \
count                      5810                                  5811   
unique                        4                                     1   
top               institutional                                    []   
freq                       5161                                  5811   
mean                        NaN                                   NaN   
std                         NaN                                   NaN   
min                         NaN                                   NaN   
25%                         NaN                                   NaN   
50%                         NaN                                   NaN   
75%                         NaN                                   NaN   
max                         NaN                                   NaN   

       system_metadata.date_modified system_metadata.date_created  \
count                           5811                         5811   
unique                           171                         5643   
top              2022-01-12 15:35:47          2020-09-18 12:53:48   
freq                              73                           81   
mean                             NaN                          NaN   
std                              NaN                          NaN   
min                              NaN                          NaN   
25%                              NaN                          NaN   
50%                              NaN                          NaN   
75%                              NaN                          NaN   
max                              NaN                          NaN   

                  

In [6]:
opendoar_df.isna().sum()

system_metadata.id                              0
repository_metadata.name                        0
repository_metadata.alternativename          3656
repository_metadata.url                         1
repository_metadata.description              5811
repository_metadata.type                        1
repository_metadata.content_languages           0
system_metadata.date_modified                   0
system_metadata.date_created                    0
repository_metadata.content_subjects          167
repository_metadata.content_types             144
organization                                    0
policy_urls                                     0
repository_metadata.software                    0
repository_metadata.oai_url                  1364
system_metadata.publicly_visible                0
repository_metadata.repository_status        5811
repository_metadata.fulltext_record_count    3519
repository_metadata.metadata_record_count    1627
dtype: int64

In [7]:
pd.DataFrame(opendoar_df['repository_metadata.content_types'].explode()).groupby('repository_metadata.content_types').size()

repository_metadata.content_types
bibliographic_references             858
books_chapters_and_sections         2246
conference_and_workshop_papers      2037
datasets                             427
journal_articles                    4069
learning_objects                     807
other_special_item_types            1800
patents                              200
software                             105
theses_and_dissertations            3377
unpub_reports_and_working_papers    1953
dtype: int64